In [2]:
import os
from glob import glob
import robosuite as suite
import numpy as np

In [7]:
import h5py
from PIL import Image, ImageSequence
import io
from IPython.display import Image as IPImage

# Load the HDF5 file
# file_path = os.path.join(dir, 'demo.hdf5')
def load_hdf5_data(f, level=0, print_hierarchy=True):
    """Loads data from an HDF5 file into a dictionary.

    Args:
        file_path (str): The path to the HDF5 file.
        level (int): The current level of nesting (for printing hierarchy).

    Returns:
        dict: A dictionary containing the loaded data, organized by dataset names.
    """

    data = {}
    for key in f.keys():
        dataset = f[key]
        data[key] = {}

        if isinstance(dataset, h5py.Group):
            # Handle nested groups
            if 'demo' in dataset.name and 'demo_0' not in dataset.name :
                print_hierarchy=False
            if print_hierarchy:
                indent = "  " * level
                print(f"{indent}{key}/")
            data[key] = load_hdf5_data(dataset, level + 1, print_hierarchy)
        else:
            # Handle datasets
            if print_hierarchy:
                indent = "  " * level
                print(f"{indent}{key}: {dataset.shape} type:{dataset.dtype}")
            data[key]['data'] = dataset[:]
            data[key]['attributes'] = dict(dataset.attrs)
    return data


# with h5py.File(files[0], 'r') as f:
#     print("Keys: %s" % f.keys())
#     a_group_key = list(f.keys())[0]

#     # get list of the demos keys
#     demo_keys = list(f[a_group_key])

#     # Load the demonstration data into variables for each demonstration
#     print("Keys: %s" % f[a_group_key][demo_keys[0]].keys())
#     for demo_key in demo_keys:
#         print(demo_key)
#         demos.append(f[a_group_key][demo_key][:])


In [9]:
# first test with hdf5 file from libero:

# Load the HDF5 file
print("current dir: ", os.getcwd())

hdf5_file = '/home/balloch/data/libero/datasets/libero_90/KITCHEN_SCENE5_put_the_black_bowl_on_the_plate_demo.hdf5'
with h5py.File(hdf5_file, 'r') as f:
    loaded_data = load_hdf5_data(f, print_hierarchy=True)

hdf5_file_new = '/home/balloch/data/libero/datasets/rand_libero_90/rand_start_KITCHEN_SCENE1_put_the_black_bowl_on_the_plate_demo.hdf5'
with h5py.File(hdf5_file_new, 'r') as f2:
    loaded_data2 = load_hdf5_data(f2, print_hierarchy=True)


current dir:  /home/balloch/code/sheeprl/scripts
data/
  demo_0/
    actions: (131, 7) type:float64
    dones: (131,) type:uint8
    obs/
      agentview_rgb: (131, 128, 128, 3) type:uint8
      ee_ori: (131, 3) type:float64
      ee_pos: (131, 3) type:float64
      ee_states: (131, 6) type:float64
      eye_in_hand_rgb: (131, 128, 128, 3) type:uint8
      gripper_states: (131, 2) type:float64
      joint_states: (131, 7) type:float64
    rewards: (131,) type:uint8
    robot_states: (131, 9) type:float64
    states: (131, 64) type:float64
data/
  demo_0/
    actions: (123, 8) type:float64
    dones: (123,) type:uint8
    obs/
      agentview_rgb: (123, 128, 128, 3) type:uint8
      ee_ori: (123, 3) type:float64
      ee_pos: (123, 3) type:float64
      ee_states: (123, 6) type:float64
      eye_in_hand_rgb: (123, 128, 128, 3) type:uint8
      gripper_states: (123, 2) type:float64
      joint_states: (123, 7) type:float64
    rewards: (123,) type:uint8
    robot_states: (123, 9) type:fl

In [11]:
import h5py
import cv2
import numpy as np
import os
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML


def hdf5_to_mp4(hdf5_file_path, output_directory, dataset_name='agentview_rgb', fps=30):
    # Create output directory if it doesn't exist
    os.makedirs(output_directory, exist_ok=True)

    with h5py.File(hdf5_file_path, 'r') as f:
        data_group = f['data']

        for demo_name in data_group.keys():
            demo_group = data_group[demo_name]

            if 'obs' in demo_group and dataset_name in demo_group['obs']:
                frames = demo_group['obs'][dataset_name][:]

                # Ensure frames are in uint8 format
                if frames.dtype != np.uint8:
                    frames = (frames * 255).astype(np.uint8)

                # Get video dimensions
                height, width, _ = frames.shape[1:]

                # Create video writer object
                output_file = os.path.join(output_directory, f"{demo_name}_{dataset_name}.mp4")
                fourcc = cv2.VideoWriter_fourcc(*'mp4v')
                out = cv2.VideoWriter(output_file, fourcc, fps, (width, height))

                # Write frames to video
                for frame in frames:
                    # OpenCV uses BGR color format
                    frame_bgr = cv2.cvtColor(frame, cv2.COLOR_RGB2BGR)
                    out.write(frame_bgr)

                # Release video writer
                out.release()

                print(f"Video saved: {output_file}")
            else:
                print(f"Dataset '{dataset_name}' not found in {demo_name}/obs")

# if __name__ == "__main__":
#     hdf5_file_path = "path/to/your/hdf5_file.h5"
#     output_directory = "path/to/output/directory"
#     dataset_name = "agentview_rgb"  # Change this if you want to use a different dataset

def hdf5_to_animation(hdf5_file_path, dataset_name='agentview_rgb', demo_index=0, interval=33):
    with h5py.File(hdf5_file_path, 'r') as f:
        data_group = f['data']
        demo_names = list(data_group.keys())

        if demo_index >= len(demo_names):
            raise ValueError(f"Demo index {demo_index} is out of range. There are only {len(demo_names)} demos.")

        demo_name = demo_names[demo_index]
        demo_group = data_group[demo_name]

        if 'obs' in demo_group and dataset_name in demo_group['obs']:
            frames = demo_group['obs'][dataset_name][:]

            # Ensure frames are in uint8 format
            if frames.dtype != np.uint8:
                frames = (frames * 255).astype(np.uint8)

            fig, ax = plt.subplots(figsize=(8, 8))
            ax.axis('off')
            im = ax.imshow(frames[0])

            def update(frame):
                im.set_array(frame)
                return [im]

            anim = FuncAnimation(fig, update, frames=frames, interval=interval, blit=True)
            plt.close(fig)  # Prevent duplicate display in notebooks

            return HTML(anim.to_jshtml())
        else:
            print(f"Dataset '{dataset_name}' not found in {demo_name}/obs")
            return None


In [13]:
# test rendering video animation
dataset_name = "agentview_rgb"  # Change this if you want to use a different dataset
demo_index = 0  # Change this to select a different demo

animation = hdf5_to_animation(hdf5_file_new, dataset_name, demo_index)
if animation:
    display(animation)


In [ ]:
# test saving file:

dataset_name = "agentview_rgb"  # Change this if you want to use a different dataset
output_directory = '/home/balloch/data/libero'
hdf5_to_mp4(hdf5_file, output_directory, dataset_name)

In [5]:
loaded_data['data']['demo_9']['states']['data'].shape

(64, 45)

In [6]:
# Create a list of images from the numpy array
images = [Image.fromarray(frame) for frame in data]

# Save the images as a GIF
gif_path = 'animation.gif'
images[0].save(gif_path, save_all=True, append_images=images[1:], loop=0, duration=100)

# Display the GIF in the Jupyter Notebook
IPImage(filename=gif_path)

NameError: name 'data' is not defined

In [3]:
print("current dir: ", os.getcwd())

dir='../demonstration_data/random_STUDY_SCENE1_pick_up_the_book_and_place_it_in_the_left_compartment_of_the_caddy.bddl_1729033541_234288'

print(os.path.join(dir,'*'))
files = [os.path.abspath(file) for file in glob(os.path.join(dir, '*'))]
# files = glob(os.path.join(dir,'*'))
print(files)

current dir:  /home/balloch/code/sheeprl/scripts
../demonstration_data/random_STUDY_SCENE1_pick_up_the_book_and_place_it_in_the_left_compartment_of_the_caddy.bddl_1729033541_234288/*
['/home/balloch/code/sheeprl/demonstration_data/random_STUDY_SCENE1_pick_up_the_book_and_place_it_in_the_left_compartment_of_the_caddy.bddl_1729033541_234288/demo.hdf5']
